In [2]:
"""
Processing the data
"""
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler, MinMaxScaler


def process_data(train, test, lags):
    """Process data
    Reshape and split train\test data.

    # Arguments
        train: String, name of .csv train file.
        test: String, name of .csv test file.
        lags: integer, time lag.
    # Returns
        X_train: ndarray.
        y_train: ndarray.
        X_test: ndarray.
        y_test: ndarray.
        scaler: StandardScaler.
    """
    attr = 'VFlow'
    df1 = pd.read_csv(train, encoding='utf-8').fillna(0)
    df2 = pd.read_csv(test, encoding='utf-8').fillna(0)

    # scaler = StandardScaler().fit(df1[attr].values)
    scaler = MinMaxScaler(feature_range=(0, 1)).fit(df1[attr].values.reshape(-1, 1))
    flow1 = scaler.transform(df1[attr].values.reshape(-1, 1)).reshape(1, -1)[0]
    flow2 = scaler.transform(df2[attr].values.reshape(-1, 1)).reshape(1, -1)[0]

    train, test = [], []
    for i in range(lags, len(flow1)):
        train.append(flow1[i - lags: i + 1])
    for i in range(lags, len(flow2)):
        test.append(flow2[i - lags: i + 1])

    train = np.array(train)
    test = np.array(test)
    np.random.shuffle(train)

    X_train = train[:, :-1]
    y_train = train[:, -1]
    X_test = test[:, :-1]
    y_test = test[:, -1]

    return X_train, y_train, X_test, y_test, scaler

In [3]:
def train_model(model, X_train, y_train, name, scats_number, config):
    """train
    train a single model.

    # Arguments
        model: Model, NN model to train.
        X_train: ndarray(number, lags), Input data for train.
        y_train: ndarray(number, ), result data for train.
        name: String, name of model.
        config: Dict, parameter for train.
    """

    model.compile(loss="mse", optimizer="rmsprop", metrics=['mape'])
    # early = EarlyStopping(monitor='val_loss', patience=30, verbose=0, mode='auto')
    hist = model.fit(
        X_train, y_train,
        batch_size=config["batch"],
        epochs=config["epochs"],
        validation_split=0.05,
        verbose=0)

    #Create folder structure: model/<model_name>/<scats_number>
    model_folder = f'model/{name}/{scats_number}'
    os.makedirs(model_folder, exist_ok=True)

    #Save the model and loss history
    model.save(f'{model_folder}/{name}_{scats_number}.h5')
    df = pd.DataFrame.from_dict(hist.history)
    df.to_csv(f'{model_folder}/{name}_{scats_number}_loss.csv', encoding='utf-8', index=False)

In [4]:
import os

def do_train(model_name):
    lag = 12
    config = {"batch": 256, "epochs": 500}

    train_folder = 'intersection/train/'
    test_folder = 'intersection/test/'

    for filename in os.listdir(train_folder):
        if filename.endswith(".csv"):
            scats_number = filename.split('_')[1].split('.')[0]
            train_file = os.path.join(train_folder, filename)
            test_file = os.path.join(test_folder, f"test_{scats_number}.csv")

            print(f"Processing SCATS Number: {scats_number}")

            X_train, y_train, X_test, y_test, scaler = process_data(train_file, test_file, lag)

            model_file_name = model_name

            if model_name == 'lstm':
                X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1], 1))
                m = get_lstm([12, 64, 64, 1])
                train_model(m, X_train, y_train, model_file_name, scats_number, config)

            elif model_name == 'gru':
                X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1], 1))
                m = get_gru([12, 64, 64, 1])
                train_model(m, X_train, y_train, model_file_name, scats_number, config)

            elif model_name == 'saes':
                X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1]))
                m = get_saes([12, 400, 400, 400, 1])
                train_seas(m, X_train, y_train, model_file_name, scats_number, config)
            
            elif model_name == 'nt_saes':
                X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1]))
                m = get_nt_saes([12, 400, 400, 400, 1])
                train_nt_saes(m, X_train, y_train, model_file_name, scats_number, config)

            print(f"Saved model for SCATS Number: {scats_number}")


In [5]:
"""
Defination of NN model
"""
from keras.layers import Dense, Dropout, Activation
from keras.layers import Input, LSTM, GRU, Dense 
from keras.models import Sequential


def get_lstm(units):
    """LSTM(Long Short-Term Memory)
    Build LSTM Model.

    # Arguments
        units: List(int), number of input, output and hidden units.
    # Returns
        model: Model, nn model.
    """

    model = Sequential()
    model.add(Input(shape=(units[0], 1)))
    model.add(LSTM(units[1], return_sequences=True))
    model.add(LSTM(units[2]))
    model.add(Dropout(0.2))
    model.add(Dense(units[3], activation='sigmoid'))

    return model


def get_gru(units):
    """GRU(Gated Recurrent Unit)
    Build GRU Model.

    # Arguments
        units: List(int), number of input, output and hidden units.
    # Returns
        model: Model, nn model.
    """

    model = Sequential()
    model.add(GRU(units[1], input_shape=(units[0], 1), return_sequences=True))
    model.add(GRU(units[2]))
    model.add(Dropout(0.2))
    model.add(Dense(units[3], activation='sigmoid'))

    return model


def _get_nt_sae(inputs, hidden, output):
    """SAE(Auto-Encoders)
    Build SAE Model.

    # Arguments
        inputs: Integer, number of input units.
        hidden: Integer, number of hidden units.
        output: Integer, number of output units.
    # Returns
        model: Model, nn model.
    """

    model = Sequential()
    model.add(Dense(hidden, input_dim=inputs, name='hidden'))
    model.add(Activation('sigmoid'))
    model.add(Dropout(0.2))
    model.add(Dense(output, activation='sigmoid'))

    return model


def get_nt_saes(layers):
    """SAEs(Stacked Auto-Encoders)
    Build SAEs Model.

    # Arguments
        layers: List(int), number of input, output and hidden units.
    # Returns
        models: List(Model), List of SAE and SAEs.
    """
    sae1 = _get_nt_sae(layers[0], layers[1], layers[-1])
    sae2 = _get_nt_sae(layers[1], layers[2], layers[-1])
    sae3 = _get_nt_sae(layers[2], layers[3], layers[-1])

    saes = Sequential()
    saes.add(Dense(layers[1], input_dim=layers[0], name='hidden1'))
    saes.add(Activation('sigmoid'))
    saes.add(Dense(layers[2], name='hidden2'))
    saes.add(Activation('sigmoid'))
    saes.add(Dense(layers[3], name='hidden3'))
    saes.add(Activation('sigmoid'))
    saes.add(Dropout(0.2))
    saes.add(Dense(layers[4], activation='sigmoid'))

    models = [sae1, sae2, sae3, saes]

    return models

In [6]:
def train_nt_saes(models, X_train, y_train, name, scats_number, config):
    """train
    train the SAEs model.

    # Arguments
        models: List, list of SAE model.
        X_train: ndarray(number, lags), Input data for train.
        y_train: ndarray(number, ), result data for train.
        name: String, name of model.
        config: Dict, parameter for train.
    """

    temp = X_train
    # early = EarlyStopping(monitor='val_loss', patience=30, verbose=0, mode='auto')

    for i in range(len(models) - 1):
        if i > 0:
            p = models[i - 1]
            hidden_layer_model = Model(inputs=p.inputs,
                                       outputs=p.get_layer('hidden').output)
            temp = hidden_layer_model.predict(temp)

        m = models[i]
        m.compile(loss="mse", optimizer="rmsprop", metrics=['mape'])

        m.fit(temp, y_train, batch_size=config["batch"],
              epochs=config["epochs"],
              validation_split=0.05)

        models[i] = m

    saes = models[-1]
    for i in range(len(models) - 1):
        weights = models[i].get_layer('hidden').get_weights()
        saes.get_layer('hidden%d' % (i + 1)).set_weights(weights)

    train_model(saes, X_train, y_train, name, scats_number, config)

## warning: this stuff will take ages to run and needs GPU time

In [7]:
from keras.models import Model
from keras.callbacks import EarlyStopping

In [8]:
do_train('sae')

Processing SCATS Number: 2000
Saved model for SCATS Number: 2000
Processing SCATS Number: 2200
Saved model for SCATS Number: 2200
Processing SCATS Number: 2820
Saved model for SCATS Number: 2820
Processing SCATS Number: 2825
Saved model for SCATS Number: 2825
Processing SCATS Number: 2827
Saved model for SCATS Number: 2827
Processing SCATS Number: 2846
Saved model for SCATS Number: 2846
Processing SCATS Number: 3001
Saved model for SCATS Number: 3001
Processing SCATS Number: 3002
Saved model for SCATS Number: 3002
Processing SCATS Number: 3120
Saved model for SCATS Number: 3120
Processing SCATS Number: 3122
Saved model for SCATS Number: 3122
Processing SCATS Number: 3126
Saved model for SCATS Number: 3126
Processing SCATS Number: 3127
Saved model for SCATS Number: 3127
Processing SCATS Number: 3180
Saved model for SCATS Number: 3180
Processing SCATS Number: 3662
Saved model for SCATS Number: 3662
Processing SCATS Number: 3682
Saved model for SCATS Number: 3682
Processing SCATS Number: 

In [9]:
do_train('nt_saes')

Processing SCATS Number: 2000
Epoch 1/500


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


29/29 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - loss: 0.0760 - mape: 500907.5312 - val_loss: 0.0411 - val_mape: 667784.3750
Epoch 2/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0392 - mape: 377037.3750 - val_loss: 0.0299 - val_mape: 532512.8125
Epoch 3/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0301 - mape: 288116.6875 - val_loss: 0.0223 - val_mape: 567885.8125
Epoch 4/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0262 - mape: 235804.3906 - val_loss: 0.0220 - val_mape: 367084.6562
Epoch 5/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0236 - mape: 96772.1016 - val_loss: 0.0202 - val_mape: 326431.5625
Epoch 6/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0205 - mape: 159452.4062 - val_loss: 0.0165 - val_mape: 333350.1250
Epoch 7/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0194 - mape: 193701.6406 - val_loss: 0.0166 - val_mape: 295037.1875
Epoch 8/500
29/29 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - loss: 0.0183 - mape: 161986.6406 - val_loss: 0.0166 - val

Saved model for SCATS Number: 2000
Processing SCATS Number: 2200
Epoch 1/500


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

Saved model for SCATS Number: 4063
Processing SCATS Number: 4262
Epoch 1/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 2s 67ms/step - loss: 0.0500 - mape: 146499.2188 - val_loss: 0.0414 - val_mape: 231.1227
Epoch 2/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0439 - mape: 452219.7812 - val_loss: 0.0353 - val_mape: 251.3466
Epoch 3/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0383 - mape: 80114.1172 - val_loss: 0.0343 - val_mape: 211.0162
Epoch 4/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0354 - mape: 98940.0000 - val_loss: 0.0295 - val_mape: 225.9809
Epoch 5/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - loss: 0.0330 - mape: 79407.7344 - val_loss: 0.0275 - val_mape: 244.5603
Epoch 6/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0316 - mape: 212436.0938 - val_loss: 0.0252 - val_mape: 227.2709
Epoch 7/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 0.0299 - mape: 97683.0938 - val_loss: 0.0262 - val_mape: 251.9412
Epoch 8/500
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - loss: 0.0288

Saved model for SCATS Number: 4262
Processing SCATS Number: 4263


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 2s 31ms/step - loss: 0.0806 - mape: 119100.6094 - val_loss: 0.0343 - val_mape: 279.2864
Epoch 2/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - loss: 0.0408 - mape: 278686.0625 - val_loss: 0.0235 - val_mape: 220.0307
Epoch 3/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - loss: 0.0306 - mape: 318320.2188 - val_loss: 0.0179 - val_mape: 193.3502
Epoch 4/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - loss: 0.0260 - mape: 119884.9375 - val_loss: 0.0142 - val_mape: 153.9692
Epoch 5/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - loss: 0.0229 - mape: 41223.0430 - val_loss: 0.0123 - val_mape: 140.0006
Epoch 6/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - loss: 0.0201 - mape: 195151.1094 - val_loss: 0.0123 - val_mape: 145.1614
Epoch 7/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - loss: 0.0204 - mape: 143299.6562 - val_loss: 0.0102 - val_mape: 107.6535
Epoch 8/500
26/26 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - loss: 0.0179 - mape: 68768.3750 - val_loss: 0.0111 - val_mape: 87

KeyboardInterrupt: 

START NEXT TRAIN FROM HERE!!!!!!!!!!!!!!!!

In [10]:
do_train('gru')

Processing SCATS Number: 2000


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Saved model for SCATS Number: 2000
Processing SCATS Number: 2200


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Saved model for SCATS Number: 2200
Processing SCATS Number: 2820


...

C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Saved model for SCATS Number: 4812
Processing SCATS Number: 4821


C:\Users\ruchi\AppData\Roaming\Python\Python311\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Saved model for SCATS Number: 4821
Processing SCATS Number: 970


Saved model for SCATS Number: 970


In [11]:
do_train('lstm')

Processing SCATS Number: 2000


NameError: name 'Input' is not defined

## end of warning

In [11]:
import math
import warnings
import numpy as np
import pandas as pd
from keras.models import load_model
from tensorflow.keras.utils import plot_model
import sklearn.metrics as metrics
import matplotlib as mpl
import matplotlib.pyplot as plt
warnings.filterwarnings("ignore")

from keras.src.legacy.saving import legacy_h5_format

In [12]:
def MAPE(y_true, y_pred):
    """Mean Absolute Percentage Error
    Calculate the mape.

    # Arguments
        y_true: List/ndarray, ture data.
        y_pred: List/ndarray, predicted data.
    # Returns
        mape: Double, result data for train.
    """

    y = [x for x in y_true if x > 0]
    y_pred = [y_pred[i] for i in range(len(y_true)) if y_true[i] > 0]

    num = len(y_pred)
    sums = 0

    for i in range(num):
        tmp = abs(y[i] - y_pred[i]) / y[i]
        sums += tmp

    mape = sums * (100 / num)

    return mape


def eva_regress(y_true, y_pred):
    """Evaluation
    evaluate the predicted resul.

    # Arguments
        y_true: List/ndarray, ture data.
        y_pred: List/ndarray, predicted data.
    """

    mape = MAPE(y_true, y_pred)
    vs = metrics.explained_variance_score(y_true, y_pred)
    mae = metrics.mean_absolute_error(y_true, y_pred)
    mse = metrics.mean_squared_error(y_true, y_pred)
    r2 = metrics.r2_score(y_true, y_pred)
    print('explained_variance_score:%f' % vs)
    print('mape:%f%%' % mape)
    print('mae:%f' % mae)
    print('mse:%f' % mse)
    print('rmse:%f' % math.sqrt(mse))
    print('r2:%f' % r2)

def plot_results(y_true, y_preds, names):
    """Plot
    Plot the true data and predicted data.

    # Arguments
        y_true: List/ndarray, ture data.
        y_pred: List/ndarray, predicted data.
        names: List, Method names.
    """
    d = '2016-3-4 00:00'
    x = pd.date_range(d, periods=96, freq='15min')

    fig = plt.figure()
    ax = fig.add_subplot(111)

    ax.plot(x, y_true, label='True Data')
    for name, y_pred in zip(names, y_preds):
        ax.plot(x, y_pred, label=name)

    plt.legend()
    plt.grid(True)
    plt.xlabel('Time of Day')
    plt.ylabel('Flow')

    date_format = mpl.dates.DateFormatter("%H:%M")
    ax.xaxis.set_major_formatter(date_format)
    fig.autofmt_xdate()


def main():
    lag = 12
    train_folder = 'intersection/train/'
    test_folder = 'intersection/test/'

    models = ['lstm', 'gru', 'sae', 'nt_saes']
    names = ['LSTM', 'GRU', 'SAE', 'NT_SAEs']

    for filename in os.listdir(train_folder):
        if filename.endswith(".csv"):
            scats_number = filename.split('_')[1].split('.')[0]
            train_file = os.path.join(train_folder, filename)
            test_file = os.path.join(test_folder, f"test_{scats_number}.csv")

            print(f"Evaluating for SCATS Number: {scats_number}")
            _, _, X_test, y_test, scaler = process_data(train_file, test_file, lag)
            y_test = scaler.inverse_transform(y_test.reshape(-1, 1)).reshape(1, -1)[0]

            y_preds = []
            for model_name in models:
                model = load_model(f"model/{model_name}/{scats_number}/{model_name}_{scats_number}.h5")
                X_test = np.reshape(X_test, (X_test.shape[0], X_test.shape[1], 1))
                predicted = model.predict(X_test)
                predicted = scaler.inverse_transform(predicted.reshape(-1, 1)).reshape(1, -1)[0]
                y_preds.append(predicted[:96])

                print(f"Evaluating {model_name} for SCATS Number: {scats_number}")
                eva_regress(y_test, predicted)

            plot_results(y_test[:96], y_preds, names)


In [13]:
main()

Evaluating for SCATS Number: 2000


TypeError: Could not locate function 'mse'. Make sure custom classes are decorated with `@keras.saving.register_keras_serializable()`. Full object config: {'module': 'keras.metrics', 'class_name': 'function', 'config': 'mse', 'registered_name': 'mse'}